## **Applio NoUI**
A simple, high-quality voice conversion tool focused on ease of use and performance.

[Support](https://discord.gg/urxFjYmYYh) — [GitHub](https://github.com/IAHispano/Applio) — [Terms of Use](https://github.com/IAHispano/Applio/blob/main/TERMS_OF_USE.md)

<br>

---

<br>

#### **Acknowledgments**

To all external collaborators for their special help in the following areas: Hina (Encryption method), Poopmaster (Extra section), Shirou (UV installer),  Kit Lemonfoot (NoUI inspiration)

#### **Disclaimer**
By using Applio, you agree to comply with ethical and legal standards, respect intellectual property and privacy rights, avoid harmful or prohibited uses, and accept full responsibility for any outcomes, while Applio disclaims liability and reserves the right to amend these terms.

### **Install Applio**
If the runtime restarts, re-run the installation steps.

In [ ]:
# @title Mount Google Drive
from google.colab import drive

drive.mount("/content/drive")

In [ ]:
# @title Setup runtime environment
from multiprocessing import cpu_count
cpu_cores = cpu_count()
post_process = False
hop_length = 128 # Common default value for hop_length, added for consistency across cells

!git config --global advice.detachedHead false
!git clone https://github.com/IAHispano/Applio --branch 3.2.9 --single-branch
%cd /content/Applio
!sudo update-alternatives --set python3 /usr/bin/python3.10
!curl -LsSf https://astral.sh/uv/install.sh | sh

print("Installing requirements...")
!uv pip install -q -r requirements.txt
print("Finished installing requirements!")
!python core.py "prerequisites" --models "True" --pretraineds_hifigan "True"

In [ ]:

# @title Unduh File Model
# @markdown Kode ini akan mengunduh file model yang diperlukan ke direktori `/content/`.

import os

# URL dan nama file
files_to_download = {
    "D_GKv1_48k.pth": "https://huggingface.co/glickko/GK_pretrain/resolve/main/D_GKv1_48k.pth?download=true",
    "G_GKv1_48k.pth": "https://huggingface.co/glickko/GK_pretrain/resolve/main/G_GKv1_48k.pth?download=true",

}

# Direktori tujuan
output_directory = "/content"

# Proses pengunduhan
for filename, url in files_to_download.items():
    output_path = os.path.join(output_directory, filename)
    print(f"Mengunduh {filename}...")
    # Menggunakan wget untuk mengunduh file
    !wget -q --show-progress -O {output_path} "{url}"
    print(f"Selesai! File disimpan di: {output_path}\n")

print("🎉 Semua file telah berhasil diunduh.")

# Menampilkan isi folder /content untuk verifikasi
print("\nIsi folder /content saat ini:")
!ls -lh /content

### **Train**

In [ ]:
# @title Setup model variables
model_name = "" # @param {type:"string"}
sample_rate = "48k"  # @param ["32k", "40k", "48k"] {allow-input: false}
sr = int(sample_rate.rstrip("k")) * 1000

In [ ]:
# @title Preprocess Dataset
from os import environ
environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
dataset_path = ""  # @param {type:"string"}

cut_preprocess = "Simple" # @param ["Skip","Simple","Automatic"]
chunk_len = 5 # @param {type:"slider", min:0.5, max:5.0, step:0.5}
overlap_len = 0.3 # @param {type:"slider", min:0, max:0.5, step:0.1}
process_effects = False # @param{type:"boolean"}
noise_reduction = False # @param{type:"boolean"}
noise_reduction_strength = 0.7 # @param {type:"slider", min:0.0, max:1.0, step:0.1}

%cd /content/Applio
!python core.py preprocess --model_name "{model_name}" --dataset_path "{dataset_path}" --sample_rate "{sr}" --cpu_cores "{cpu_cores}" --cut_preprocess "{cut_preprocess}" --process_effects "{process_effects}" --noise_reduction "{noise_reduction}" --noise_reduction_strength "{noise_reduction_strength}" --chunk_len "{chunk_len}" --overlap_len "{overlap_len}"

In [ ]:
# @title Extract Features
f0_method = "rmvpe"  # @param ["crepe", "crepe-tiny", "rmvpe"] {allow-input: false}

sr = int(sample_rate.rstrip("k")) * 1000
include_mutes = 2 # @param {type:"slider", min:0, max:10, step:1}
embedder_model = "contentvec" # @param ["contentvec", "chinese-hubert-base", "japanese-hubert-base", "korean-hubert-base", "custom"] {allow-input: false}
embedder_model_custom = "" # @param {type:"string"}

%cd /content/Applio
!python core.py extract --model_name "{model_name}" --f0_method "{f0_method}" --hop_length "{hop_length}" --sample_rate "{sr}" --cpu_cores "{cpu_cores}" --gpu "0" --embedder_model "{embedder_model}" --embedder_model_custom "{embedder_model_custom}"  --include_mutes "{include_mutes}"

In [ ]:
# @title Generate index file
index_algorithm = "Auto"  # @param ["Auto", "Faiss", "KMeans"] {allow-input: false}

%cd /content/Applio
!python core.py index --model_name "{model_name}" --index_algorithm "{index_algorithm}"

In [ ]:
# @title Start Training
import threading
import time
import os
import shutil
import hashlib
import time

LOGS_FOLDER = "/content/Applio/logs/"
GOOGLE_DRIVE_PATH = "/content/drive/MyDrive/RVC_Backup"


def import_google_drive_backup():
    print("Importing Google Drive backup...")
    for root, dirs, files in os.walk(GOOGLE_DRIVE_PATH):
        for filename in files:
            filepath = os.path.join(root, filename)
            if os.path.isfile(filepath):
                backup_filepath = os.path.join(
                    LOGS_FOLDER, os.path.relpath(filepath, GOOGLE_DRIVE_PATH)
                )
                backup_folderpath = os.path.dirname(backup_filepath)
                if not os.path.exists(backup_folderpath):
                    os.makedirs(backup_folderpath)
                    print(f"Created backup folder: {backup_folderpath}", flush=True)
                shutil.copy2(filepath, backup_filepath)
                print(f"Imported file from Google Drive backup: {filename}")
    print("Google Drive backup import completed.")


if "autobackups" not in globals():
    autobackups = False
# @markdown ### 💾 AutoBackup
cooldown = 15  # @param {type:"slider", min:0, max:100, step:0}
auto_backups = True  # @param{type:"boolean"}
def backup_files():
    print("\nStarting backup loop...")
    last_backup_timestamps_path = os.path.join(
        LOGS_FOLDER, "last_backup_timestamps.txt"
    )
    fully_updated = False

    while True:
        try:
            updated_files = 0
            deleted_files = 0
            new_files = 0
            last_backup_timestamps = {}

            try:
                with open(last_backup_timestamps_path, "r") as f:
                    last_backup_timestamps = dict(line.strip().split(":") for line in f)
            except FileNotFoundError:
                pass

            for root, dirs, files in os.walk(LOGS_FOLDER):
                # Excluding "zips" and "mute" directories
                if "zips" in dirs:
                    dirs.remove("zips")
                if "mute" in dirs:
                    dirs.remove("mute")

                for filename in files:
                    if filename != "last_backup_timestamps.txt":
                        filepath = os.path.join(root, filename)
                        if os.path.isfile(filepath):
                            backup_filepath = os.path.join(
                                GOOGLE_DRIVE_PATH,
                                os.path.relpath(filepath, LOGS_FOLDER),
                            )
                            backup_folderpath = os.path.dirname(backup_filepath)
                            if not os.path.exists(backup_folderpath):
                                os.makedirs(backup_folderpath)
                            last_backup_timestamp = last_backup_timestamps.get(filepath)
                            current_timestamp = os.path.getmtime(filepath)
                            if (
                                last_backup_timestamp is None
                                or float(last_backup_timestamp) < current_timestamp
                            ):
                                shutil.copy2(filepath, backup_filepath)
                                last_backup_timestamps[filepath] = str(current_timestamp)
                                if last_backup_timestamp is None:
                                    new_files += 1
                                else:
                                    updated_files += 1


            for filepath in list(last_backup_timestamps.keys()):
                if not os.path.exists(filepath):
                    backup_filepath = os.path.join(
                        GOOGLE_DRIVE_PATH, os.path.relpath(filepath, LOGS_FOLDER)
                    )
                    if os.path.exists(backup_filepath):
                        os.remove(backup_filepath)
                        deleted_files += 1
                    del last_backup_timestamps[filepath]


            if updated_files > 0 or deleted_files > 0 or new_files > 0:
                print(f"Backup Complete: {new_files} new, {updated_files} updated, {deleted_files} deleted.")
                fully_updated = False
            elif not fully_updated:
                print("Files are up to date.")
                fully_updated = True

            with open(last_backup_timestamps_path, "w") as f:
                for filepath, timestamp in last_backup_timestamps.items():
                    f.write(f"{filepath}:{timestamp}\n")

            time.sleep(cooldown if fully_updated else 0.1)


        except Exception as error:
            print(f"An error occurred during backup: {error}")


if autobackups:
    autobackups = False
    print("Autobackup Disabled")
else:
    autobackups = True
    print("Autobackup Enabled")
# @markdown ### ⚙️ Train Settings
total_epoch = 150  # @param {type:"integer"}
batch_size = 19  # @param {type:"slider", min:1, max:25, step:0}
gpu = 0
sr = int(sample_rate.rstrip("k")) * 1000
pretrained = True  # @param{type:"boolean"}
cleanup = False  # @param{type:"boolean"}
cache_data_in_gpu = False  # @param{type:"boolean"}
vocoder = "HiFi-GAN" # @param ["HiFi-GAN"]
checkpointing = False
tensorboard = True  # @param{type:"boolean"}
# @markdown ### ➡️ Choose how many epochs your model will be stored
save_every_epoch = 10  # @param {type:"slider", min:1, max:100, step:0}
save_only_latest = True  # @param{type:"boolean"}
save_every_weights = True  # @param{type:"boolean"}
overtraining_detector = False  # @param{type:"boolean"}
overtraining_threshold = 50  # @param {type:"slider", min:1, max:100, step:0}
# @markdown ### ❓ Optional
# @markdown In case you select custom pretrained, you will have to download the pretraineds and enter the path of the pretraineds.
custom_pretrained = True  # @param{type:"boolean"}
g_pretrained_path = "/content/G_GKv1_48k.pth"  # @param {type:"string"}
d_pretrained_path = "/content/D_GKv1_48k.pth"  # @param {type:"string"}

if "pretrained" not in globals():
    pretrained = True

if "custom_pretrained" not in globals():
    custom_pretrained = False

if "g_pretrained_path" not in globals():
    g_pretrained_path = "Custom Path"

if "d_pretrained_path" not in globals():
    d_pretrained_path = "Custom Path"


def start_train():
    if tensorboard == True:
        %load_ext tensorboard
        %tensorboard --logdir /content/Applio/logs/
    %cd /content/Applio
    !python core.py train --model_name "{model_name}" --save_every_epoch "{save_every_epoch}" --save_only_latest "{save_only_latest}" --save_every_weights "{save_every_weights}" --total_epoch "{total_epoch}" --sample_rate "{sr}" --batch_size "{batch_size}" --gpu "{gpu}" --pretrained "{pretrained}" --custom_pretrained "{custom_pretrained}" --g_pretrained_path "{g_pretrained_path}" --d_pretrained_path "{d_pretrained_path}" --overtraining_detector "{overtraining_detector}" --overtraining_threshold "{overtraining_threshold}" --cleanup "{cleanup}" --cache_data_in_gpu "{cache_data_in_gpu}" --vocoder "{vocoder}" --checkpointing "{checkpointing}"


server_thread = threading.Thread(target=start_train)
server_thread.start()

if auto_backups:
    backup_files()
else:
    while True:
        time.sleep(10)

In [ ]:
# @title Export model
from pathlib import Path

export_for = "training" # @param ["training", "inference"] {allow-input: false}

logs_folder = Path(f"/content/Applio/logs/{model_name}/")
if not (logs_folder.exists() and logs_folder.is_dir()):
    raise FileNotFoundError(f"{model_name} model folder not found")

%cd {logs_folder}/..
if export_for == "training":
  !zip -r "/content/{model_name}.zip" "{model_name}"
else:
  # find latest trained weight file
  !ls -t "{model_name}/{model_name}"_*e_*s.pth | head -n 1 > /tmp/weight.txt
  weight_path = open("/tmp/weight.txt", "r").read().strip()
  if weight_path == "":
    raise FileNotFoundError("Model has no weight file, please finish training first")
  weight_name = Path(weight_path).name
  # command does not fail if index is missing, and i allow it
  !zip "/content/{model_name}.zip" "{model_name}/{weight_name}" "{model_name}/{model_name}.index"

BACKUP_PATH = "/content/drive/MyDrive/RVC_Backup/"
if Path("/content/drive").is_mount():
  !mkdir -p "{BACKUP_PATH}"
  !mv "/content/{model_name}.zip" "{BACKUP_PATH}" && echo "Exported model as {BACKUP_PATH}{model_name}.zip"
else:
  !echo "Drive not mounted, exporting model as /content/{model_name}.zip"

### **Resume training**

In [ ]:
# @title Load a Backup
from google.colab import drive
import os
import shutil

# @markdown Put the exact name you put as your Model Name in Applio.
modelname = "My-Project"  # @param {type:"string"}
source_path = "/content/drive/MyDrive/RVC_Backup/" + modelname
destination_path = "/content/Applio/logs/" + modelname
backup_timestamps_file = "last_backup_timestamps.txt"
if not os.path.exists(source_path):
    print(
        "The model folder does not exist. Please verify the name is correct or check your Google Drive."
    )
else:
    time_ = os.path.join("/content/drive/MyDrive/RVC_Backup/", backup_timestamps_file)
    time__ = os.path.join("/content/Applio/logs/", backup_timestamps_file)
    if os.path.exists(time_):
        shutil.copy(time_, time__)
    shutil.copytree(source_path, destination_path)
    print("Model backup loaded successfully.")

In [ ]:
# @title Set training variables
# @markdown ### ➡️ Use the same as you did previously
model_name = "Darwin"  # @param {type:"string"}
sample_rate = "40k"  # @param ["32k", "40k", "48k"] {allow-input: false}
f0_method = "rmvpe"  # @param ["crepe", "crepe-tiny", "rmvpe"] {allow-input: false}
sr = int(sample_rate.rstrip("k")) * 1000